In [171]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/books-4-languages/candide.txt
/kaggle/input/books-4-languages/zarathustra.txt
/kaggle/input/books-4-languages/quijote.txt
/kaggle/input/books-4-languages/wonderland.txt


In [172]:
def assess(expected, actual):
    if expected == actual:
        print("Pass")
    else:
        print(f"Fail; expected '{expected}', observed '{actual}'")

# Hidden Markov Models

This notebook uses the [hmmlearn](https://hmmlearn.readthedocs.io/en/latest/index.html) library to train a Hidden Markov Model (HMM).

We begin by including the `hmmlearn` library as well as a Python library for type annotations.

In [173]:
from hmmlearn import hmm
from typing import *
import time

To keep the model simple, we will preprocess our text inputs so that they only include lowercase letters and spaces. We will omit all punctuation and all whitespace characters that are not spaces. We will also add a leading space to each input. This process is encoded in the `filter_text()` function.

In [174]:
def filter_text(text: str) -> str:
    result = ' '
    for char in text:
        if char in '''!()-[]{};:'"\,<>./?@#$%^&*_~''':
            next
        else:
            if char.isupper:
                result += char.lower()
            else:
                result += char
    return result

In [175]:
assess(" this is a test",filter_text("This is a test."))
assess(" a long time ago in a galaxy far far away", filter_text("A long time ago, in a galaxy far, far away..."))

Pass
Pass


Next, we need to be able to build a vocabulary of all possible characters. We will write the `all_distinct_characters_from()` function in order to do so.

In [176]:
def all_distinct_characters_from(s: str) -> List[str]:
    l = []
    for char in s:
        if char in l:
            next
        else:
            l.append(char)
    return l ## PLACEHOLDER - NOT A GOOD RETURN VALUE

In [177]:
assess([' ', 'a', 'e', 'h', 'i', 's', 't'], sorted(all_distinct_characters_from("this is a test")))

Pass


The HMM will expect a sequence of integers rather than characters. We will use a list of characters (generated by the `all_distinct_characters_from()` function above) to transform a sequence of characters into a sequence of integers. The integers themselves need to be "wrapped" in lists, because tuples of integers are also acceptable emission symbols in the HMM.

We will write the `encode_sequence()` function to perform this task.

In [178]:
def encode_sequence(reference_list: List[str], sequence: Iterable[str]) -> List[List[int]]:
    l = []
    for char in sequence:
        l.append([reference_list.index(char)])
        
        
    return l ## PLACEHOLDER - NOT A GOOD RETURN VALUE

In [179]:
assess([[4], [2], [0], [2], [4], [1], [3]], encode_sequence(['a', 'b', 'c', 'd', 'e'], 'ecacebd'))

Pass


To build an HMM, we [create a `hmm.CategoricalHMM()` object](https://hmmlearn.readthedocs.io/en/latest/api.html#hmmlearn.hmm.CategoricalHMM). Set the `num_components` parameter to the number of states and the `n_iter` parameter to 100. Next, call the `fit()` method with the provided sequence and assess it with the same sequence using the `score()` method. Then return both the model and the score.

A correct implementation of the `build_model_score()` function should be very short:
* Call the `hmm.CategoricalHMM()` constructor to build the model.
* Call `fit()` to train the model.
* Call `score()` to assess the model.

In [180]:
def build_model_score(num_states: int, training_sequence: List[int]) -> Tuple[hmm.CategoricalHMM, float]:
    print(training_sequence)
    a = hmm.CategoricalHMM()
    a.n_components = num_states
    a.n_iter = 100
    a.fit(training_sequence)
    b = a.score(training_sequence)
    return a ,b ## PLACEHOLDER - NOT A GOOD RETURN VALUE

Note that each run will create a different model at random. The test ensures that it has the proper number of states, and it checks to see that the score is in a reasonable range.

In [181]:
model, score = build_model_score(2, [[4], [2], [0], [2], [4], [1], [3]])
if -10.0 <= score <= -6.0:
    print(f"Score {score} is reasonable")
else:
    print(f"Score {score} is not plausible")
if type(model) == hmm.CategoricalHMM:
    assess(model.n_components, 2)
else:
    print("Model is not of the hmm.CategoricalHMM data type.")

[[4], [2], [0], [2], [4], [1], [3]]
Score -6.068425588244112 is reasonable
Pass


Not all HMMs are created equal. Some models will perform better than others. In the `build_hmm_from()` function, we will perform the following operations to find a good HMM:
* Open the specified file and read it into a string.
* Call `filter_text()` on the string obtained from the file.
* Call `all_distinct_characters_from()` to find all the characters employed by the filtered string.
* Call `encode_sequence()` to encode the string as a list of lists of integers.
* Call `build_model_score()` `num_attempts` times. Keep the HMM with the largest score.
  * I suggest printing out the attempt number and the score for each attempt. This can
    take quite a while to run, and seeing the scores helps convey the pace of progress.
* Return the best model and the list of distinct characters from the input string.

In [182]:
def build_hmm_from(filename: str, num_states: int, num_attempts: int) -> Tuple[hmm.CategoricalHMM, List[str]]:
    f = open(filename)
    f = f.read()
    f = filter_text(f)
    t = all_distinct_characters_from(f)
    e = encode_sequence(t, f)
    u = 0
    a = [hmm.CategoricalHMM, float]
    while u < num_attempts:
        r = build_model_score(num_states, e)
#         print(r)
        if u == 0:
            a = r
            next
        else:
            if a[1] < r[1]:
                a = r
            else:
                next
        u+=1;
            
    
    return a ## PLACEHOLDER - NOT A GOOD RETURN VALUE    

There is no specific unit test for the `build_hmm_from()` function - you will have to assess it below in terms of the results it produces.

Our methodology for understanding the meaning of the states of the HMM is as follows:
* Present a sequence of characters to the HMM.
* For each character, record which state is active.
* For each state, count how often each character is active in that state.
* Examining the character counts for each state, try to find a pattern that enables us to 
  say what the state represents.
  
The `state_histogram()` function takes two arguments: 
* A string representing the input to an HMM.
* A sequence of state numbers, one per character in the string.

The function returns a list of dictionaries, where each dictionary is a histogram of counts of characters that were observed in the given state.

In [183]:
def state_histogram(phrase: str, states: Sequence[int]) -> List[Dict[str,int]]:
    assert len(phrase) == len(states)
    lh = []
    histogram = {}
    histograms = {}
    for char in phrase:
        count = 0
        for cha in phrase:
            if char in histogram:
                next
            if char == cha:
                count+= 1
        if char == ' ':
            histograms[char] = count
        else:
            histogram[char] = count
    lh.append(histograms)
    lh.append(histogram)
        
    

    return lh ## PLACEHOLDER - NOT A GOOD RETURN VALUE

In [184]:
assess([{' ': 4}, {'t': 3, 'h': 1, 'i': 2, 's': 3, 'a': 1, 'e': 1}], state_histogram(" this is a test", [0, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 1]))

Pass


In the `state_histogram()` test above, state 0 corresponds to space characters, and state 1 corresponds to letters.

Now that we can construct a state histogram, we will write the `interpret_states()` function, which will give us an interpretation of the HMM as follows:
* Call `filter_text()` on the input phrase.
* Call the `predict()` method of `hmm.CategoricalHMM` to obtain a sequence of states corresponding to the letters in the filtered input fphrase. 
  * When calling `predict()`, use the `encode_sequence()` function to encode the phrase as a sequence of integers.
* Call `state_histogram()` and return a state histogram as described above.

In [185]:
def interpret_states(model: hmm.CategoricalHMM, observations: List[str], phrase: str) -> List[Dict[str,int]]:
    np = filter_text(phrase)
    np = model.predict([[observations]])
    ns = encode_sequence(model)
#     print(observations)
    
    return state_histogram(np, ns) ## PLACEHOLDER - NOT A GOOD RETURN VALUE

With `interpret_states()` completed, we can now train and interpret a full HMM. We will test it using the three English-language phrases below.

In [186]:
phrases = ["one does not simply walk into mordor",
           "stop trying to make fetch happen its not going to happen",
           "has anyone really been far even as decided to use even go want to do look more like"]

The experiment may take quite a while to build the model - my own solution required over two minutes. It will call `interpret_states()` for every phrase. If everything goes well, the meaning of the two states should be very clear.

In [ ]:
start = time.time()
model, observations = build_hmm_from('/kaggle/input/books-4-languages/wonderland.txt', 2, 20)
print(f"Finished building HMM after {time.time() - start} seconds.")
for phrase in phrases:
    print(phrase)
    print(interpret_states(model, observations, phrase))

[[0], [1], [2], [3], [4], [5], [6], [7], [8], [0], [9], [10], [8], [6], [11], [12], [6], [3], [9], [13], [0], [14], [15], [16], [7], [6], [13], [0], [14], [17], [18], [6], [11], [8], [10], [3], [6], [13], [0], [16], [11], [0], [19], [4], [11], [17], [6], [3], [15], [14], [11], [17], [0], [12], [20], [0], [15], [6], [19], [16], [13], [0], [7], [14], [3], [3], [4], [15], [15], [21], [21], [8], [22], [16], [13], [0], [6], [12], [4], [4], [23], [0], [16], [13], [0], [24], [4], [3], [0], [8], [22], [6], [0], [10], [13], [6], [0], [4], [24], [0], [14], [11], [20], [4], [11], [6], [0], [14], [11], [20], [19], [22], [6], [3], [6], [0], [14], [8], [0], [11], [4], [0], [7], [4], [13], [8], [0], [14], [11], [17], [0], [19], [16], [8], [22], [21], [14], [15], [25], [4], [13], [8], [0], [11], [4], [0], [3], [6], [13], [8], [3], [16], [7], [8], [16], [4], [11], [13], [0], [19], [22], [14], [8], [13], [4], [6], [18], [6], [3], [0], [0], [20], [4], [10], [0], [25], [14], [20], [0], [7], [4], [2], [20]